# Для тренировки модели нужно установить turicreate
Linux or mac
python 3.6 - 3.8

`pip install turicreate`

### На вход:
- _attend_features.csv (с нашими фичами)
- _groups.csv

### Выход:
- predicts/predict_v01.csv


In [1]:
import turicreate as tc
import pandas as pd

In [2]:
actions = tc.SFrame.read_csv('_attend_features.csv')

Finished parsing file /media/vasiliev/SSD_Data/_dev/ezee_may_2003/ds/_attend_features.csv

Parsing completed. Parsed 100 lines in 0.210095 secs.

------------------------------------------------------
Inferred types from first 100 line(s) of file as 
column_type_hints=[int,int,int,float,str,str,str,float,str,str,str,str,float,float,str,int,str,float,float]
If parsing fails due to incorrect types, you can correct
the inferred type list above and pass it to read_csv in
the column_type_hints argument
------------------------------------------------------


Read 173459 lines. Lines per second: 647951

Finished parsing file /media/vasiliev/SSD_Data/_dev/ezee_may_2003/ds/_attend_features.csv

Parsing completed. Parsed 600390 lines in 0.855843 secs.

### Делим общую таблицу на фичи для attend, users, groups

In [3]:
print(actions.head)
actions1 = actions[['group_id',
                    'user_id',
                    'log_visits',
                    'user_lat',
                    'user_long',
                    'направление 1',
                    'направление 2',
                    'направление 3',
                    'weekend']]

users_1 = actions[['user_id',
                   'sex','age',
                   'user_address',
                   'user_lat',
                   'user_long']]

groups_1 = actions[['group_id',
                    'lat',
                    'long',
                    'направление 1',
                    'направление 2',
                    'is_online',
                    'weekend',
                    'lesson_length',
                    'session']]

<bound method SFrame.head of Columns:
	X1	int
	group_id	int
	user_id	int
	log_visits	float
	направление 3	str
	is_online	str
	weekend	str
	lesson_length	float
	session	str
	направление 1	str
	направление 2	str
	group_address	str
	lat	float
	long	float
	sex	str
	age	int
	user_address	str
	user_lat	float
	user_long	float

Rows: 600390

Data:
+----+-----------+-----------+--------------------+---------------+-----------+
| X1 |  group_id |  user_id  |     log_visits     | направление 3 | is_online |
+----+-----------+-----------+--------------------+---------------+-----------+
| 0  | 801346549 | 101370217 | 2.0794415416798357 |  Здорово жить |  offline  |
| 1  | 801346549 | 101375025 | 3.044522437723423  |  Здорово жить |  offline  |
| 2  | 801346549 | 101392971 |        0.0         |  Здорово жить |  offline  |
| 3  | 801346550 | 101352023 | 4.1588830833596715 |  ОНЛАЙН Цигун |   online  |
| 4  | 801346550 | 101354499 | 4.1588830833596715 |  ОНЛАЙН Цигун |   online  |
| 5  | 801346550 |

There are a variety of machine learning techniques that can be used to build a recommender model. Turi Create provides a method turicreate.recommender.create that will automatically choose an appropriate model for your data set. More details on choosing a model: https://apple.github.io/turicreate/docs/userguide/recommender/choosing-a-model.html

First we create a random split of the data to produce a validation set that can be used to evaluate the model.

### Чему учим модель

Мы учим модель предсказывать логарифм от количества посещений юзером курса (логарифм потому что разброс посещений курса пользователем высокий - от 1 до 64)

### Создание и обучение дефолтной модели

In [4]:
training_data, validation_data = tc.recommender.util.random_split_by_user(actions1, 'user_id', 'group_id', item_test_proportion = 0.01)

model = tc.recommender.create(training_data,
                              'user_id',
                              'group_id',
                              target = 'log_visits',
                              user_data = users_1,
                              item_data = groups_1
                             )


Preparing data set.

Data has 600249 observations with 50906 users and 24535 items.

Data prepared in: 0.668728s

Training ranking_factorization_recommender for recommendations.

+--------------------------------+--------------------------------------------------+----------+

...

+---------+--------------+-------------------+-----------------------+-------------+

Optimization Complete: Maximum number of passes through the data reached.

Computing final objective value and training RMSE.

Final objective value: 0.619925

Final training RMSE: 0.681663

In [5]:
# параметры модели
model

Class                            : RankingFactorizationRecommender

Schema
------
User ID                          : user_id
Item ID                          : group_id
Target                           : log_visits
Additional observation features  : 6
User side features               : ['user_id', 'sex', 'age', 'user_address', 'user_lat', 'user_long']
Item side features               : ['group_id', 'lat', 'long', 'направление 1', 'направление 2', 'is_online', 'weekend', 'lesson_length', 'session']

Statistics
----------
Number of observations           : 600249
Number of users                  : 50906
Number of items                  : 24535

Training summary
----------------
Training time                    : 20.1815

Model Parameters
----------------
Model class                      : RankingFactorizationRecommender
num_factors                      : 32
binary_target                    : 0
side_data_factorization          : 1
solver                           : auto
nmf               

### Получение предсказаний от дефолтной модели

In [6]:
default_recommendations = model.recommend()

recommendations finished on 1000/50906 queries. users per second: 947.634

recommendations finished on 2000/50906 queries. users per second: 951.438

recommendations finished on 3000/50906 queries. users per second: 954.758

recommendations finished on 4000/50906 queries. users per second: 956.493

recommendations finished on 5000/50906 queries. users per second: 957.426

...

recommendations finished on 46000/50906 queries. users per second: 933.69

recommendations finished on 47000/50906 queries. users per second: 909.727

recommendations finished on 48000/50906 queries. users per second: 885.189

recommendations finished on 49000/50906 queries. users per second: 862.79

recommendations finished on 50000/50906 queries. users per second: 842.345

### Посмотрим рекоммендации для отдельных юзеров

In [7]:
df_groups = pd.read_csv('groups.csv')

def display_history_and_predictions_for_user(user_id, train_dataset, predictions):
    print('----------------------------------------------------------------------------')
    print('User', user_id, 'history:')
    display(train_dataset[train_dataset['user_id'] == user_id][
        'group_id','is_online','session','направление 1','направление 2'])
    predictions = predictions[predictions['user_id'] == user_id].to_dataframe()
    print('User recommendations:')
    predicted_groups = predictions['group_id'].to_list()
    display(df_groups[df_groups['уникальный номер'].isin(predicted_groups)].drop(columns=[
        'адрес площадки','расписание в активных периодах','расписание в закрытых периодах','расписание в плановом периоде']))

In [8]:
user_id = 101352882

display_history_and_predictions_for_user(user_id, actions, default_recommendations)

----------------------------------------------------------------------------
User 101352882 history:


Columns:
	group_id	int
	is_online	str
	session	str
	направление 1	str
	направление 2	str

Rows: Unknown

Data:
+-----------+-----------+---------+-----------------------+
|  group_id | is_online | session |     направление 1     |
+-----------+-----------+---------+-----------------------+
| 801348234 |   online  |  mornig | Физическая активность |
| 801348838 |  offline  |  mornig | Физическая активность |
| 801348944 |  offline  |  mornig |         Танцы         |
| 801349048 |  offline  |  mornig | Физическая активность |
| 801350227 |   online  |  mornig |       Творчество      |
| 801350380 |   online  |  mornig |         Танцы         |
| 801351413 |   online  |  mornig |       Рисование       |
| 801358464 |   online  |  mornig | Физическая активность |
| 801358465 |   online  |  mornig |         Танцы         |
| 801358466 |   online  |  mornig | Физическая активность |
+-----------+-----------+---------+-----------------------+
+-------------------------------+
|         направление 2         |
+-------------------------------+
|       ОНЛАЙН Гимнастика       |
|           Гимнастика          |
|             Танцы             |
|              ОФП              |
| ОНЛАЙН Художественно-прикл... |
|          ОНЛАЙН Танцы         |
|        ОНЛАЙН Рисование       |
|       ОНЛАЙН Гимнастика       |
|          ОНЛАЙН Танцы         |
|       ОНЛАЙН Гимнастика       |
+-------------------------------+
[? rows x 5 columns]
Note: Only the head of the SFrame is printed. This SFrame is lazily evaluated.
You can use sf.materialize() to force materialization.

User recommendations:


уникальный номер                        направление 1   
1715          801349571                Физическая активность  \
1940          801353947  Спецпроект / Серебряный университет   
1941          801354781  Спецпроект / Серебряный университет   
5007          801351512                                 Игры   
8237          801348983                Физическая активность   
11484         801352857                Физическая активность   
12964         801358897  Спецпроект / Серебряный университет   
17517         801364900  Спецпроект / Серебряный университет   
22168         801363716  Спецпроект / Серебряный университет   
22169         801365403  Спецпроект / Серебряный университет   

                       направление 2   
1715                      ОНЛАЙН ОФП  \
1940   ОНЛАЙН Серебряный университет   
1941   ОНЛАЙН Серебряный университет   
5007          ОНЛАЙН Настольные игры   
8237                      Гимнастика   
11484                     Гимнастика   
12964         Серебряный университет   
17517         Серебряный университет   
22168         Серебряный университет   
22169         Серебряный университет   

                                           направление 3   
1715         ОНЛАЙН Физкультурно-оздоровительные занятия  \
1940          ОНЛАЙН Педагог дополнительного образования   
1941   ОНЛАЙН Предпринимательская деятельность в мало...   
5007                         ОНЛАЙН Иные настольные игры   
8237                                Суставная гимнастика   
11484    Дыхательная гимнастика по системе Стрельниковой   
12964                                    Экскурсоведение   
17517                                    Экскурсоведение   
22168                                 Интернет-маркетинг   
22169                      Компьютерная графика и дизайн   

                                округ площадки   
1715    Северо-Западный административный округ  \
1940              Южный административный округ   
1941              Южный административный округ   
5007       Юго-Западный административный округ   
8237       Юго-Западный административный округ   
11484  Северо-Восточный административный округ   
12964  Северо-Восточный административный округ   
17517  Северо-Восточный административный округ   
22168          Северный административный округ   
22169          Северный административный округ   

                          район площадки  
1715        муниципальный округ Строгино  
1940         муниципальный округ Донской  
1941         муниципальный округ Донской  
5007        муниципальный округ Коньково  
8237   муниципальный округ Академический  
11484      муниципальный округ Ростокино  
12964      муниципальный округ Ростокино  
17517      муниципальный округ Ростокино  
22168          муниципальный округ Сокол  
22169          муниципальный округ Сокол

In [9]:
user_id = 101354253

display_history_and_predictions_for_user(user_id, actions, default_recommendations)

----------------------------------------------------------------------------
User 101354253 history:


Columns:
	group_id	int
	is_online	str
	session	str
	направление 1	str
	направление 2	str

Rows: Unknown

Data:
+-----------+-----------+-----------+-----------------------+-------------------+
|  group_id | is_online |  session  |     направление 1     |   направление 2   |
+-----------+-----------+-----------+-----------------------+-------------------+
| 801347802 |   online  |   mornig  | Физическая активность |     ОНЛАЙН ОФП    |
| 801348667 |   online  |  evening  | Физическая активность | ОНЛАЙН Гимнастика |
| 801348794 |   online  |   mornig  | Физическая активность | ОНЛАЙН Гимнастика |
| 801349796 |  offline  |   mornig  | Физическая активность |     Гимнастика    |
| 801349875 |  offline  | aftennoon | Физическая активность |     Гимнастика    |
| 801350556 |   online  |   mornig  | Физическая активность |     ОНЛАЙН ОФП    |
| 801350568 |   online  |   mornig  | Физическая активность |     ОНЛАЙН ОФП    |
| 801361065 |  offline  |   mornig  |       Рисование       |     Рисование     |
+-----------+-----------+-----------+-----------------------+-------------------+
[? rows x 5 columns]
Note: Only the head of the SFrame is printed. This SFrame is lazily evaluated.
You can use sf.materialize() to force materialization.

User recommendations:


уникальный номер                        направление 1   
1708         801347075                Физическая активность  \
1715         801349571                Физическая активность   
1730         801348933                Физическая активность   
1735         801348433                Физическая активность   
1749         801351282                Физическая активность   
1762         801351112                Физическая активность   
1769         801348457                Физическая активность   
1940         801353947  Спецпроект / Серебряный университет   
5007         801351512                                 Игры   
5617         801352452                Физическая активность   

                      направление 2   
1708                     ОНЛАЙН ОФП  \
1715                     ОНЛАЙН ОФП   
1730                     ОНЛАЙН ОФП   
1735                     ОНЛАЙН ОФП   
1749                     ОНЛАЙН ОФП   
1762                     ОНЛАЙН ОФП   
1769                     ОНЛАЙН ОФП   
1940  ОНЛАЙН Серебряный университет   
5007         ОНЛАЙН Настольные игры   
5617                     ОНЛАЙН ОФП   

                                    направление 3   
1708  ОНЛАЙН Физкультурно-оздоровительные занятия  \
1715  ОНЛАЙН Физкультурно-оздоровительные занятия   
1730  ОНЛАЙН Физкультурно-оздоровительные занятия   
1735  ОНЛАЙН Физкультурно-оздоровительные занятия   
1749  ОНЛАЙН Физкультурно-оздоровительные занятия   
1762  ОНЛАЙН Физкультурно-оздоровительные занятия   
1769  ОНЛАЙН Физкультурно-оздоровительные занятия   
1940   ОНЛАЙН Педагог дополнительного образования   
5007                  ОНЛАЙН Иные настольные игры   
5617                  ОНЛАЙН Лечебная физкультура   

                              округ площадки   
1708  Северо-Западный административный округ  \
1715  Северо-Западный административный округ   
1730         Западный административный округ   
1735     Юго-Западный административный округ   
1749            Южный административный округ   
1762         Западный административный округ   
1769       Северный административный округ,    
1940            Южный административный округ   
5007     Юго-Западный административный округ   
5617         Западный административный округ   

                              район площадки  
1708              муниципальный округ Щукино  
1715            муниципальный округ Строгино  
1730           муниципальный округ Можайский  
1735             муниципальный округ Ясенево  
1749  муниципальный округ Бирюлево Восточное  
1762    муниципальный округ Ново-Переделкино  
1769             муниципальный округ Сокол,   
1940             муниципальный округ Донской  
5007            муниципальный округ Коньково  
5617      муниципальный округ Фили-Давыдково

In [10]:
user_id = 101385865

display_history_and_predictions_for_user(user_id, actions, default_recommendations)

----------------------------------------------------------------------------
User 101385865 history:


Columns:
	group_id	int
	is_online	str
	session	str
	направление 1	str
	направление 2	str

Rows: Unknown

Data:
+-----------+-----------+-----------+-----------------------+
|  group_id | is_online |  session  |     направление 1     |
+-----------+-----------+-----------+-----------------------+
| 801346923 |   online  |   mornig  |         Танцы         |
| 801348309 |   online  |   mornig  |       Творчество      |
| 801348946 |   online  |   mornig  | Физическая активность |
| 801349093 |   online  |   mornig  |      Образование      |
| 801350488 |  offline  | aftennoon | Физическая активность |
| 801350739 |  offline  |   mornig  |         Танцы         |
| 801350759 |  offline  |   mornig  |         Танцы         |
| 801351106 |   online  |   mornig  |       Творчество      |
| 801351519 |  offline  |   mornig  |         Танцы         |
| 801351888 |  offline  |   mornig  |         Танцы         |
+-----------+-----------+-----------+-----------------------+
+--------------------------+
|      направление 2       |
+--------------------------+
|       ОНЛАЙН Танцы       |
|  ОНЛАЙН Красота и стиль  |
|    ОНЛАЙН Гимнастика     |
| ОНЛАЙН Иностранные языки |
|    Фитнес, тренажеры     |
|          Танцы           |
|          Танцы           |
|  ОНЛАЙН Красота и стиль  |
|          Танцы           |
|          Танцы           |
+--------------------------+
[? rows x 5 columns]
Note: Only the head of the SFrame is printed. This SFrame is lazily evaluated.
You can use sf.materialize() to force materialization.

User recommendations:


уникальный номер                        направление 1   
1715          801349571                Физическая активность  \
1762          801351112                Физическая активность   
1940          801353947  Спецпроект / Серебряный университет   
4296          801353977                Физическая активность   
5007          801351512                                 Игры   
11484         801352857                Физическая активность   
12964         801358897  Спецпроект / Серебряный университет   
17517         801364900  Спецпроект / Серебряный университет   
22168         801363716  Спецпроект / Серебряный университет   
22169         801365403  Спецпроект / Серебряный университет   

                       направление 2   
1715                      ОНЛАЙН ОФП  \
1762                      ОНЛАЙН ОФП   
1940   ОНЛАЙН Серебряный университет   
4296                            Лыжи   
5007          ОНЛАЙН Настольные игры   
11484                     Гимнастика   
12964         Серебряный университет   
17517         Серебряный университет   
22168         Серебряный университет   
22169         Серебряный университет   

                                         направление 3   
1715       ОНЛАЙН Физкультурно-оздоровительные занятия  \
1762       ОНЛАЙН Физкультурно-оздоровительные занятия   
1940        ОНЛАЙН Педагог дополнительного образования   
4296                                              Лыжи   
5007                       ОНЛАЙН Иные настольные игры   
11484  Дыхательная гимнастика по системе Стрельниковой   
12964                                  Экскурсоведение   
17517                                  Экскурсоведение   
22168                               Интернет-маркетинг   
22169                    Компьютерная графика и дизайн   

                                          округ площадки   
1715              Северо-Западный административный округ  \
1762                     Западный административный округ   
1940                        Южный административный округ   
4296   Юго-Восточный административный округ, Юго-Вост...   
5007                 Юго-Западный административный округ   
11484            Северо-Восточный административный округ   
12964            Северо-Восточный административный округ   
17517            Северо-Восточный административный округ   
22168                    Северный административный округ   
22169                    Северный административный округ   

                                          район площадки  
1715                        муниципальный округ Строгино  
1762                муниципальный округ Ново-Переделкино  
1940                         муниципальный округ Донской  
4296   муниципальный округ Некрасовка, муниципальный ...  
5007                        муниципальный округ Коньково  
11484                      муниципальный округ Ростокино  
12964                      муниципальный округ Ростокино  
17517                      муниципальный округ Ростокино  
22168                          муниципальный округ Сокол  
22169                          муниципальный округ Сокол

### Делаем сравнение различных моделей

Описание всех моделей, заложенных в turicreate, доступно по ссылке:

https://apple.github.io/turicreate/docs/api/turicreate.toolkits.recommender.html

In [11]:
print('---------------\nTrain default model')
model_0 = tc.recommender.create(training_data, 'user_id', 'group_id', target = 'log_visits',
                                user_data = users_1, item_data = groups_1)

print('---------------\nTrain item_similarity model')
model_1 = tc.item_similarity_recommender.create(training_data, 'user_id', 'group_id', target = 'log_visits',
                                                user_data = users_1, item_data = groups_1)

print('---------------\nTrain item_similarity model')
model_1 = tc.item_similarity_recommender.create(training_data, 'user_id', 'group_id',
                                                user_data = users_1, item_data = groups_1)


print('---------------\nTrain popularity_recommender model')
model_2 = tc.popularity_recommender.create(training_data, 'user_id', 'group_id', target = 'log_visits',
                                           user_data = users_1, item_data = groups_1)

print('---------------\nTrain factorization_recommender model')
model_3 = tc.factorization_recommender.create(training_data, 'user_id', 'group_id', target = 'log_visits',
                                              user_data = users_1, item_data = groups_1)

print('---------------\nTrain ranking_factorization_recommender model')
model_4 = tc.ranking_factorization_recommender.create(training_data, 'user_id', 'group_id', target = 'log_visits',
                                                      user_data = users_1, item_data = groups_1)

---------------
Train default model


Preparing data set.

Data has 600249 observations with 50906 users and 24535 items.

Data prepared in: 0.728263s

Training ranking_factorization_recommender for recommendations.

...

+---------+--------------+-------------------+-----------------------+-------------+

Optimization Complete: Maximum number of passes through the data reached.

Computing final objective value and training RMSE.

Final objective value: 0.447343

Final training RMSE: 0.580203

In [12]:
print(tc.recommender.util.compare_models(
    validation_data, 
    [model_0, model_1,model_2,model_3,model_4], 
    model_names=["Default model",
                 "Item similarity model",
                 'Popularity recommender',
                 'Factorization recommender',
                 'Ranking factorization recommender']))

PROGRESS: Evaluate model Default model

Precision and recall summary statistics by cutoff
+--------+----------------+-------------+
| cutoff | mean_precision | mean_recall |
+--------+----------------+-------------+
|   1    |      0.0       |     0.0     |
|   2    |      0.0       |     0.0     |
|   3    |      0.0       |     0.0     |
|   4    |      0.0       |     0.0     |
|   5    |      0.0       |     0.0     |
|   6    |      0.0       |     0.0     |
|   7    |      0.0       |     0.0     |
|   8    |      0.0       |     0.0     |
|   9    |      0.0       |     0.0     |
|   10   |      0.0       |     0.0     |
+--------+----------------+-------------+
[10 rows x 3 columns]




Overall RMSE: 1.007039673637151

Per User RMSE (best)
+-----------+----------------------+-------+
|  user_id  |         rmse         | count |
+-----------+----------------------+-------+
| 101363028 | 0.003518587396161621 |   1   |
+-----------+----------------------+-------+
[1 rows x 3 columns]


Per User RMSE (worst)
+-----------+--------------------+-------+
|  user_id  |        rmse        | count |
+-----------+--------------------+-------+
| 101386423 | 2.9526192023109195 |   1   |
+-----------+--------------------+-------+
[1 rows x 3 columns]


Per Item RMSE (best)
+-----------+----------------------+-------+
|  group_id |         rmse         | count |
+-----------+----------------------+-------+
| 801372028 | 0.003518587396161621 |   1   |
+-----------+----------------------+-------+
[1 rows x 3 columns]


Per Item RMSE (worst)
+-----------+--------------------+-------+
|  group_id |        rmse        | count |
+-----------+--------------------+-------+
| 801348843 | 2.9

`Default model:             `Overall RMSE: 1.06 -> 1.01

`Item similarity model:     `Overall RMSE: 1.93 -> 1.98

`Popularity recommender:    `Overall RMSE: 0.98 -> 0.99

`Factorization recommender: `Overall RMSE: 1.00 -> 1.02

`Ranking factorization:     `Overall RMSE: 1.16 -> 0.97

### Сохраняем результаты Ranking factirozation модели

In [13]:
preds = model_4.recommend(k=10)
display(preds)

recommendations finished on 1000/50906 queries. users per second: 959.311

recommendations finished on 2000/50906 queries. users per second: 958.769

recommendations finished on 3000/50906 queries. users per second: 963.23

recommendations finished on 4000/50906 queries. users per second: 966.774

recommendations finished on 5000/50906 queries. users per second: 967.934

...

recommendations finished on 47000/50906 queries. users per second: 968.863

recommendations finished on 48000/50906 queries. users per second: 966.095

recommendations finished on 49000/50906 queries. users per second: 921.562

recommendations finished on 50000/50906 queries. users per second: 852.434

Columns:
	user_id	int
	group_id	int
	score	float
	rank	int

Rows: 509060

Data:
+-----------+-----------+----------------------+------+
|  user_id  |  group_id |        score         | rank |
+-----------+-----------+----------------------+------+
| 101426550 | 801352677 | -0.2971672095655973  |  1   |
| 101426550 | 801350648 | -0.38607383737154133 |  2   |
| 101426550 | 801353947 | -0.39573670042226605 |  3   |
| 101426550 | 801350374 | -0.40850518637148303 |  4   |
| 101426550 | 801350588 | -0.45679765715146026 |  5   |
| 101426550 | 801352685 | -0.5234787665202614  |  6   |
| 101426550 | 801354781 | -0.5332328782133018  |  7   |
| 101426550 | 801348664 | -0.6083739495584277  |  8   |
| 101426550 | 801347287 | -0.6241699730561101  |  9   |
| 101426550 | 801373704 | -0.6408761484663823  |  10  |
+-----------+-----------+----------------------+------+
[509060 rows x 4 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

### Сохраняем результаты для бэка

In [14]:
preds.to_dataframe().to_csv('predicts/predict_v01.csv', index=False )

### Делаем предсказание для Test (с выборкой предсказаний на март-апрель 2023)

In [15]:
import json
with open('groups2023.json') as json_file:
    groups2023 = json.load(json_file)

df_test = pd.read_csv('test.csv')
df_test.head()
df_test['уникальный номер участника'] = df_test['уникальный номер участника'].astype(int)


def display_history_and_predictions_for_user2(user_id, train_dataset, predictions):
    print('----------------------------------------------------------------------------')
    print('User', user_id, 'history:')
    #display(train_dataset[train_dataset['user_id'] == user_id]['group_id','is_online','session','направление 1','направление 2'].to_dataframe())
    display(train_dataset[train_dataset['user_id'] == user_id].to_dataframe())
    predictions = predictions[predictions['user_id'] == user_id]
    print('User recommendations:')
    predicted_groups = predictions['group_id'].to_list()
    display(df_groups[df_groups['уникальный номер'].isin(predicted_groups)].drop(columns=[
        'адрес площадки',
        'расписание в активных периодах',
        'расписание в закрытых периодах',
        'расписание в плановом периоде']))

In [16]:
results = [] 


def get_groups_mix(user_id):
    # Predictions
    x0 = model_0.recommend(users=[user_id], k=1000).to_dataframe()
    x0 = x0[x0['group_id'].isin(groups2023)]
    x0 = x0.head(10)
    
    x1 = model_1.recommend(users=[user_id], k=1000).to_dataframe()
    x1 = x1[x1['group_id'].isin(groups2023)]
    x1 = x1.head(2)
    
    x2 = model_2.recommend(users=[user_id], k=1000).to_dataframe()
    x2 = x2[x2['group_id'].isin(groups2023)]
    x2 = x2.head(10)
    
    x3 = model_3.recommend(users=[user_id], k=1000).to_dataframe()
    x3 = x3[x3['group_id'].isin(groups2023)]
    x3 = x3.head(1)
    
    x4 = model_4.recommend(users=[user_id], k=1000).to_dataframe()
    x4 = x4[x4['group_id'].isin(groups2023)]
    x4 = x4.head(2)
    
    # Отбираем 10 штук, чтобы 1 была от 3 алгоритма и 2 от 4 алгоритма
    x = pd.concat([x1, x3, x0])
    x = x.drop_duplicates(subset='group_id').head(10) 
    
    return x
    
       

for index, row in df_test.iterrows():
    # Получаем юзера
    user_id = row['уникальный номер участника']
    
    x = get_groups_mix(user_id)
    
    display_history_and_predictions_for_user2(user_id, training_data, x)

    groups_list = x['group_id'].to_list()
    groups_list = [str(x) for x in groups_list]    
    groups_str = ','.join(groups_list)
    results.append(groups_str)
 

----------------------------------------------------------------------------
User 101346610 history:


group_id    user_id  log_visits   user_lat  user_long направление 1   
0   801347805  101346610    3.526361  55.976343  37.159629         Танцы  \
1   801352817  101346610    3.526361  55.976343  37.159629         Танцы   
2   801352824  101346610    1.098612  55.976343  37.159629         Танцы   
3   801352838  101346610    4.382027  55.976343  37.159629         Танцы   
4   801352862  101346610    4.356709  55.976343  37.159629         Танцы   
5   801357011  101346610    1.098612  55.976343  37.159629         Танцы   
6   801357012  101346610    1.098612  55.976343  37.159629         Танцы   
7   801361704  101346610    3.737670  55.976343  37.159629         Танцы   
8   801361706  101346610    3.737670  55.976343  37.159629         Танцы   
9   801361928  101346610    2.397895  55.976343  37.159629         Танцы   
10  801362306  101346610    0.693147  55.976343  37.159629         Танцы   

   направление 2   направление 3 weekend  
0          Танцы   Бальные танцы   False  
1          Танцы   Бальные танцы    True  
2          Танцы   Бальные танцы   False  
3          Танцы  Танцы для всех   False  
4          Танцы   Бальные танцы   False  
5          Танцы   Бальные танцы   False  
6          Танцы   Бальные танцы   False  
7          Танцы  Танцы для всех   False  
8          Танцы  Танцы для всех   False  
9          Танцы  Танцы для всех   False  
10         Танцы   Бальные танцы   False

User recommendations:


уникальный номер направление 1              направление 2   
4355          801353695         Танцы                      Танцы  \
4440          801348485         Танцы                      Танцы   
4469          801357672         Танцы                      Танцы   
4586          801348853         Танцы                      Танцы   
6163          801348827         Танцы                      Танцы   
8085          801351759         Танцы                      Танцы   
8748          801353048         Танцы                      Танцы   
8750          801353046         Танцы                      Танцы   
9791          801356697   Образование  Информационные технологии   
14059         801359338          Игры            Шахматы и шашки   

                        направление 3   
4355               Классические танцы  \
4440                   Танцы для всех   
4469                    Бальные танцы   
4586                   Народные танцы   
6163                   Народные танцы   
8085                   Танцы для всех   
8748         Латиноамериканские танцы   
8750                Современные танцы   
9791   Осваиваем мобильные устройства   
14059                 Шахматы и шашки   

                                          округ площадки   
4355                Юго-Восточный административный округ  \
4440                Юго-Восточный административный округ   
4469               Зеленоградский административный округ   
4586                 Юго-Западный административный округ   
6163                 Юго-Западный административный округ   
8085                 Юго-Западный административный округ   
8748   Центральный административный округ, Центральны...   
8750   Центральный административный округ, Центральны...   
9791               Зеленоградский административный округ   
14059                Юго-Западный административный округ   

                                          район площадки  
4355                      муниципальный округ Некрасовка  
4440                       муниципальный округ Рязанский  
4469                         муниципальный округ Крюково  
4586                    муниципальный округ Южное Бутово  
6163                    муниципальный округ Южное Бутово  
8085                    муниципальный округ Южное Бутово  
8748   муниципальный округ Мещанский, муниципальный о...  
8750   муниципальный округ Мещанский, муниципальный о...  
9791                   муниципальное образование Савелки  
14059                         муниципальный округ Зюзино

----------------------------------------------------------------------------
User 101346612 history:


...

уникальный номер                        направление 1   
479           801351925                            Рисование  \
749           801355180                            Рисование   
876           801349690                            Рисование   
5139          801352655                            Рисование   
7236          801358144                                Пение   
17517         801364900  Спецпроект / Серебряный университет   
21465         801371942                          Образование   
21484         801369799                          Образование   
22168         801363716  Спецпроект / Серебряный университет   
22169         801365403  Спецпроект / Серебряный университет   

                направление 2                          направление 3   
479          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования  \
749          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
876          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
5139         ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
7236                    Пение                          Хоровое пение   
17517  Серебряный университет                        Экскурсоведение   
21465   ОНЛАЙН Пеший лекторий  ОНЛАЙН Краеведение и онлайн-экскурсии   
21484   ОНЛАЙН Пеший лекторий  ОНЛАЙН Краеведение и онлайн-экскурсии   
22168  Серебряный университет                     Интернет-маркетинг   
22169  Серебряный университет          Компьютерная графика и дизайн   

                                          округ площадки   
479              Северо-Восточный административный округ  \
749    Северный административный округ, Северный адми...   
876    Северо-Восточный административный округ, Север...   
5139                 Юго-Западный административный округ   
7236                 Юго-Западный административный округ   
17517            Северо-Восточный административный округ   
21465                                                NaN   
21484                                                NaN   
22168                    Северный административный округ   
22169                    Северный административный округ   

                                          район площадки  
479                          муниципальный округ Марфино  
749    муниципальный округ Западное Дегунино, муницип...  
876    муниципальный округ Отрадное, муниципальный ок...  
5139                    муниципальный округ Южное Бутово  
7236                    муниципальный округ Южное Бутово  
17517                      муниципальный округ Ростокино  
21465                                                NaN  
21484                                                NaN  
22168                          муниципальный округ Сокол  
22169                          муниципальный округ Сокол

----------------------------------------------------------------------------
User 101449555 history:


Empty DataFrame
Columns: [group_id, user_id, log_visits, user_lat, user_long, направление 1, направление 2, направление 3, weekend]
Index: []

User recommendations:


уникальный номер                        направление 1   
479           801351925                            Рисование  \
749           801355180                            Рисование   
876           801349690                            Рисование   
5139          801352655                            Рисование   
7236          801358144                                Пение   
17517         801364900  Спецпроект / Серебряный университет   
21465         801371942                          Образование   
21484         801369799                          Образование   
22168         801363716  Спецпроект / Серебряный университет   
22169         801365403  Спецпроект / Серебряный университет   

                направление 2                          направление 3   
479          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования  \
749          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
876          ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
5139         ОНЛАЙН Рисование     ОНЛАЙН Различные техники рисования   
7236                    Пение                          Хоровое пение   
17517  Серебряный университет                        Экскурсоведение   
21465   ОНЛАЙН Пеший лекторий  ОНЛАЙН Краеведение и онлайн-экскурсии   
21484   ОНЛАЙН Пеший лекторий  ОНЛАЙН Краеведение и онлайн-экскурсии   
22168  Серебряный университет                     Интернет-маркетинг   
22169  Серебряный университет          Компьютерная графика и дизайн   

                                          округ площадки   
479              Северо-Восточный административный округ  \
749    Северный административный округ, Северный адми...   
876    Северо-Восточный административный округ, Север...   
5139                 Юго-Западный административный округ   
7236                 Юго-Западный административный округ   
17517            Северо-Восточный административный округ   
21465                                                NaN   
21484                                                NaN   
22168                    Северный административный округ   
22169                    Северный административный округ   

                                          район площадки  
479                          муниципальный округ Марфино  
749    муниципальный округ Западное Дегунино, муницип...  
876    муниципальный округ Отрадное, муниципальный ок...  
5139                    муниципальный округ Южное Бутово  
7236                    муниципальный округ Южное Бутово  
17517                      муниципальный округ Ростокино  
21465                                                NaN  
21484                                                NaN  
22168                          муниципальный округ Сокол  
22169                          муниципальный округ Сокол

In [17]:
df_test['уникальный номер группы'] = results
df_test.to_csv('test.csv', index=False)

In [18]:
display(df_test)

уникальный номер участника   
0                     101346610  \
1                     101346612   
2                     101347269   
3                     101347321   
4                     101347983   
..                          ...   
195                   101447423   
196                   101447935   
197                   101449373   
198                   101449505   
199                   101449555   

                               уникальный номер группы  
0    801357672,801356697,801359338,801348485,801353...  
1    801367517,801367330,801348571,801348485,801353...  
2    801362915,801366107,801348571,801349690,801358...  
3    801356697,801357672,801359338,801348485,801353...  
4    801363734,801357696,801348571,801353046,801350...  
..                                                 ...  
195  801373394,801363757,801348571,801349690,801353...  
196  801366606,801362980,801357444,801349690,801353...  
197  801362727,801363146,801348135,801352655,801349...  
198  801369799,801371942,801358144,801352655,801365...  
199  801369799,801371942,801358144,801352655,801365...  

[200 rows x 2 columns]